In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import minimize
from scipy.integrate import simps
from ed import *
from dos import *
import warnings
warnings.filterwarnings("ignore")

In [2]:
def get_G0_semicirc(omFs, mu, t):
    from dos import semicircle
    from scipy.integrate import simps
    ws = np.linspace(-2*t,2*t,1000)
    sc_dos = semicircle(ws,t)
    G0 = np.zeros(len(omFs),dtype=complex)
    for iomF, omF in enumerate(omFs):
        y = sc_dos/(1j*omF+mu-ws)
        G0[iomF] = simps(y, ws)
    return G0

In [3]:
def get_G0_aim(omFs, V, eb, ed, mu):
    G0_aim = np.zeros(len(omFs),dtype=complex)
    for iomF, omF in enumerate(omFs):
        Delta = 0.0
        for ib in range(eb.shape[0]):
            Delta += (V[ib]*np.conj(V[ib])).real/(1j*omF-eb[ib])
        G0_aim[iomF] = 1./(1j*omF - ed + mu - Delta)
    return G0_aim

def get_G0w_aim(ws, eta, V, eb, ed, mu):
    G0_aim = np.zeros((len(ws)),dtype=complex)
    for iw, w in enumerate(ws):
        Delta = 0.0
        for ib in range(eb.shape[0]):
            Delta += (V[ib]*np.conj(V[ib])).real/(w + 1j*eta - eb[ib])
        G0_aim[iw] = (1./(w + 1j*eta - ed + mu - Delta))[0]
    return G0_aim

In [4]:
def cost_func(x, *args):
    omFs, ed, mu, G0, Nb, Nmax = args
    V = x[:Nb] + 1j*x[Nb:2*Nb]
    eb = x[2*Nb:3*Nb]
    G0_aim = get_G0_aim(omFs, V, eb, ed ,mu)
    cost = 0.0
    for iomF in range(Nmax):
        diff = 1./G0_aim[iomF] - 1./G0[iomF]
        cost += (np.conj(diff)*diff).real/omFs[iomF]**1
    return cost 

In [5]:
np.random.seed(1234)
np.set_printoptions(suppress=True, precision=8)

# initial density of state
T = 0.005
t = 0.5
mu = 0.0
Nb = 3
Nmax = 100
NomF = Nmax
omFs = (2*np.arange(NomF)+1)*np.pi*T
G0 = get_G0_semicirc(omFs, mu, t)

no = 2*(1+Nb)
print('no=',no)
FH_list = build_fermion_op(no)
print(len(FH_list))
FH_list_dense = [np.array(FH.todense(),dtype=complex) for FH in FH_list]

ebs = np.random.uniform(-1,1,Nb)
Vrs = np.random.uniform(-0.5,0.5,Nb)
Vis = np.zeros((Nb))
x0 = np.hstack((Vrs,Vis,ebs))
mix = 0.3
maxit = 500

Us = np.arange(2.0,4.02,0.02)[::-1]
  
doccs = []
for U in Us:
    it = 0
    diff = 1e20
    while diff > 5e-5 and it<maxit:
        print("-------------------------------------- it=%d U=%.2f --------------------------------------"%(it, U))

        # fit V eb
        args = omFs, 0.0, mu, G0, Nb, Nmax
        result = minimize(cost_func,x0,args=args, method='L-BFGS-B', options={'gtol': 1e-2, 'eps': 1e-12})
        print("GA root convergence message---------------------------------")
        print("sucess=",result.success)
        print(result.message)
        V = result.x[:Nb] + 1j*result.x[Nb:2*Nb]
        eb = result.x[2*Nb:3*Nb]
        x0 = result.x
        print('V=',V)
        print('eb=', eb)
    
        # ED part
        h1 = np.array([[-U/2+mu, 0.0],
                        [ 0.0,-U/2+mu]])
        eb = np.kron(eb,np.ones((2)))
        V = np.kron(V,np.eye(2)).T
        #
        V2E = np.zeros((2,2,2,2))
        V2E[1,1,0,0] = U
        V2E[0,0,1,1] = U
        print('V(ED)=',V)
        print('eb(ED)=', eb)

        dm, evals, evecs, docc = solve_Hemb_thermal(T, h1, V, eb, V2E, FH_list, verbose=0)
        
        print('dm=')
        print(dm.real)
        print('trace(dm)=',np.trace(dm).real)
        print('docc=', docc.real)
    
        GomF = compute_GomF_thermal(T, omFs, evals, evecs, FH_list_dense)
      
        # update G0
        G0_new = 1./(1j*omFs + mu - t**2*GomF)
    
        diff = np.sum(np.abs(G0_new  -G0))
        print('diff=', diff)
        it += 1
        G0 = (1-mix)*G0 + mix*G0_new

    # real frequency quantities
    ws = np.linspace(-5,5,200) # frequency mesh
    eta = 0.1 #broadening factor
    Gw = compute_Gw_thermal(T, ws, eta, evals, evecs, FH_list_dense) # real frequency impurity Green's function
    G0w = get_G0w_aim(ws, eta, V[::2,::2], eb[::2], 0.0, mu) # real frequency non-interacting impurity Green's function
    Sigw = 1./G0w - 1./Gw # real frequency self-energy
    Glattw = compute_Glattw_semcircle(ws,eta,Sigw,mu) # real frequency lattice Green's function
    # Matsubara self-energy
    G0 = get_G0_aim(omFs, V[::2,::2], eb[::2], 0.0, mu) # matsubara frequency impurity Green's function
    Sig = 1./G0 - 1./GomF # Matsubara frequency self-energy
    Sig = 1./G0 - 1./GomF
    Z = 1./(1-(Sig[0].imag)/(omFs[0])) # quasiparticle weight estimate from Matsubara self-energy
    Glatt = compute_GlattomF_semcircle(omFs,Sig,mu) # real frequency lattice Green's function

    
    np.savetxt('Gimpw_U%.2f.dat'%(U),np.vstack((ws,Gw.real,Gw.imag)).T)
    np.savetxt('Glattw_U%.2f.dat'%(U),np.vstack((ws,Glattw.real,Glattw.imag)).T)
    np.savetxt('Gimp_U%.2f.dat'%(U), np.vstack((omFs,GomF.real,GomF.imag)).T)
    np.savetxt('Glatt_U%.2f.dat'%(U), np.vstack((omFs,Glatt.real,Glatt.imag)).T)
    np.savetxt('G0_U%.2f.dat'%(U), np.vstack((omFs,G0.real,G0.imag)).T)
    np.savetxt('Sig_U%.2f.dat'%(U), np.vstack((omFs,Sig.real,Sig.imag)).T)
    np.savetxt('Sigw_U%.2f.dat'%(U), np.vstack((ws,Sigw.real,Sigw.imag)).T)
    np.savetxt('x0_U%.2f.dat'%(U), x0)
    doccs.append(docc.real)
    print(U, dm[0,0].real, dm[1,1].real, docc.real, Z, diff)
    f = open('U_occ_docc_Z_diff_mott2metal.dat','a')
    print(U, dm[0,0].real, dm[1,1].real, docc.real, Z, diff, file=f)
    f.close()

no= 8
8
-------------------------------------- it=0 U=4.00 --------------------------------------
GA root convergence message---------------------------------
sucess= True
CONVERGENCE: REL_REDUCTION_OF_F_<=_FACTR*EPSMCH
V= [ 0.26451211+0.j  0.26451413+0.j -0.07980677+0.j]
eb= [-0.15225325  0.15225749  0.00000006]
V(ED)= [[ 0.26451211+0.j  0.        +0.j]
 [ 0.        +0.j  0.26451211+0.j]
 [ 0.26451413+0.j  0.        +0.j]
 [ 0.        +0.j  0.26451413+0.j]
 [-0.07980677+0.j -0.        +0.j]
 [-0.        +0.j -0.07980677+0.j]]
eb(ED)= [-0.15225325 -0.15225325  0.15225749  0.15225749  0.00000006  0.00000006]
Egs= -2.422852560668228
evals= [0.         0.01758063 0.01758063 0.01758097 0.01758097 0.02553739
 0.02553739 0.02553739 0.08179146 0.08179302]
dm=
[[ 0.49999996 -0.         -0.12750049 -0.         -0.12749977  0.
   0.13723702  0.        ]
 [-0.          0.49999996 -0.         -0.12750049  0.         -0.12749977
  -0.          0.13723702]
 [-0.12750049 -0.          0.90336344 -0.  

Egs= -2.833962495916429
evals= [0.         0.00451574 0.00451574 0.00453082 0.00453082 0.00604457
 0.00604457 0.00604457 0.32974018 0.33004966]
dm=
[[ 0.50000252 -0.         -0.04953689 -0.         -0.04952686  0.
   0.02499908  0.        ]
 [-0.          0.50000252 -0.         -0.04953689  0.         -0.04952686
   0.          0.02499908]
 [-0.04953689 -0.          0.99351933 -0.         -0.0000069   0.
   0.00694453 -0.        ]
 [-0.         -0.04953689 -0.          0.99351933  0.         -0.0000069
  -0.          0.00694453]
 [-0.04952686  0.         -0.0000069   0.          0.00648029 -0.
  -0.00695057 -0.        ]
 [ 0.         -0.04952686  0.         -0.0000069  -0.          0.00648029
  -0.         -0.00695057]
 [ 0.02499908  0.          0.00694453 -0.         -0.00695057 -0.
   0.50034516 -0.        ]
 [ 0.          0.02499908 -0.          0.00694453 -0.         -0.00695057
  -0.          0.50034516]]
trace(dm)= 4.000694595810131
docc= 0.009143010420129513
diff= 28.57943786296

dm=
[[ 0.49999967 -0.         -0.0459983  -0.         -0.04599966  0.
  -0.00497947  0.        ]
 [-0.          0.49999967 -0.         -0.0459983   0.         -0.04599966
   0.         -0.00497947]
 [-0.0459983  -0.          0.99557549 -0.         -0.000005    0.
  -0.00053347 -0.        ]
 [-0.         -0.0459983  -0.          0.99557549  0.         -0.000005
   0.         -0.00053347]
 [-0.04599966  0.         -0.000005    0.          0.00442487 -0.
   0.00053365 -0.        ]
 [ 0.         -0.04599966  0.         -0.000005   -0.          0.00442487
   0.          0.00053365]
 [-0.00497947  0.         -0.00053347  0.          0.00053365  0.
   0.49996653  0.        ]
 [ 0.         -0.00497947 -0.         -0.00053347 -0.          0.00053365
   0.          0.49996653]]
trace(dm)= 3.9999331056343395
docc= 0.008065077953783386
diff= 26.731874391634374
-------------------------------------- it=11 U=4.00 --------------------------------------
GA root convergence message---------------------

diff= 9.311075030800831
-------------------------------------- it=16 U=4.00 --------------------------------------
GA root convergence message---------------------------------
sucess= True
CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL
V= [ 0.32221497+0.j  0.32179803+0.j -0.0065335 +0.j]
eb= [-1.56884885  1.56626178  0.00107626]
V(ED)= [[ 0.32221497+0.j  0.        +0.j]
 [ 0.        +0.j  0.32221497+0.j]
 [ 0.32179803+0.j  0.        +0.j]
 [ 0.        +0.j  0.32179803+0.j]
 [-0.0065335 +0.j -0.        +0.j]
 [-0.        +0.j -0.0065335 +0.j]]
eb(ED)= [-1.56884885 -1.56884885  1.56626178  1.56626178  0.00107626  0.00107626]
Egs= -5.19650890081779
evals= [0.         0.         0.00100843 0.00109886 0.00109886 0.00109886
 0.0021525  0.0021525  1.27838743 1.27945241]
dm=
[[ 0.50000353  0.         -0.04615898  0.         -0.0461362  -0.
   0.00177628  0.        ]
 [ 0.          0.50000353  0.         -0.04615898 -0.         -0.0461362
  -0.          0.00177628]
 [-0.04615898  0.          

dm=
[[ 0.49999995  0.         -0.04564556  0.         -0.04564476 -0.
   0.00086715  0.        ]
 [ 0.          0.49999995  0.         -0.04564556 -0.         -0.04564476
  -0.          0.00086715]
 [-0.04564556  0.          0.99574009  0.         -0.00000341 -0.
   0.00008274  0.        ]
 [ 0.         -0.04564556  0.          0.99574009 -0.         -0.00000341
   0.          0.00008274]
 [-0.04564476 -0.         -0.00000341 -0.          0.00425981  0.
  -0.00008284  0.        ]
 [-0.         -0.04564476 -0.         -0.00000341  0.          0.00425981
   0.         -0.00008284]
 [ 0.00086715 -0.          0.00008274  0.         -0.00008284  0.
   0.45368861  0.        ]
 [ 0.          0.00086715  0.          0.00008274  0.         -0.00008284
   0.          0.45368861]]
trace(dm)= 3.9073769305910884
docc= 0.008024492139896673
diff= 1.813015930987675
-------------------------------------- it=22 U=4.00 --------------------------------------
GA root convergence message--------------------

...

dm=
[[ 0.5         0.         -0.1869276   0.         -0.1869269  -0.
   0.20773802 -0.        ]
 [ 0.          0.5        -0.         -0.1869276  -0.         -0.1869269
  -0.          0.20773802]
 [-0.1869276  -0.          0.8483707  -0.          0.00000046  0.
   0.24121705  0.        ]
 [ 0.         -0.1869276  -0.          0.8483707   0.          0.00000046
  -0.          0.24121705]
 [-0.1869269  -0.          0.00000046  0.          0.15162789  0.
  -0.24121644  0.        ]
 [-0.         -0.1869269   0.          0.00000046  0.          0.15162789
   0.         -0.24121644]
 [ 0.20773802 -0.          0.24121705 -0.         -0.24121644  0.
   0.50000061  0.        ]
 [-0.          0.20773802  0.          0.24121705  0.         -0.24121644
   0.          0.50000061]]
trace(dm)= 3.9999983771648733
docc= 0.06965299193583165
diff= 0.13213465235248753
-------------------------------------- it=11 U=2.00 --------------------------------------
GA root convergence message--------------------

diff= 0.023034363173259596
-------------------------------------- it=16 U=2.00 --------------------------------------
GA root convergence message---------------------------------
sucess= True
CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL
V= [ 0.18844579+0.j  0.18844247+0.j -0.07609964+0.j]
eb= [-0.10329974  0.10329127 -0.00000076]
V(ED)= [[ 0.18844579+0.j  0.        +0.j]
 [ 0.        +0.j  0.18844579+0.j]
 [ 0.18844247+0.j  0.        +0.j]
 [ 0.        +0.j  0.18844247+0.j]
 [-0.07609964+0.j -0.        +0.j]
 [-0.        +0.j -0.07609964+0.j]]
eb(ED)= [-0.10329974 -0.10329974  0.10329127  0.10329127 -0.00000076 -0.00000076]
Egs= -1.3506503611250027
evals= [0.         0.02282388 0.02282388 0.02282663 0.02282663 0.03813532
 0.03813532 0.03813532 0.05914757 0.05915147]
dm=
[[ 0.49999997  0.         -0.18704254  0.         -0.18704608  0.
   0.2077974   0.        ]
 [ 0.          0.49999997 -0.         -0.18704254  0.         -0.18704608
  -0.          0.2077974 ]
 [-0.18704254 -0.    

dm=
[[ 0.50000001  0.         -0.18705789  0.         -0.18706268 -0.
   0.20779457 -0.        ]
 [ 0.          0.50000001  0.         -0.18705789 -0.         -0.18706268
   0.          0.20779457]
 [-0.18705789  0.          0.84827244  0.         -0.00000661 -0.
   0.24130089 -0.        ]
 [ 0.         -0.18705789  0.          0.84827244 -0.         -0.00000661
   0.          0.24130089]
 [-0.18706268 -0.         -0.00000661 -0.          0.15174072  0.
  -0.24130867  0.        ]
 [-0.         -0.18706268 -0.         -0.00000661  0.          0.15174072
  -0.         -0.24130867]
 [ 0.20779457  0.          0.24130089  0.         -0.24130867 -0.
   0.49999262 -0.        ]
 [-0.          0.20779457 -0.          0.24130089  0.         -0.24130867
  -0.          0.49999262]]
trace(dm)= 4.000011576889512
docc= 0.06973889765007459
diff= 0.0028657708797505577
-------------------------------------- it=22 U=2.00 --------------------------------------
GA root convergence message------------------

diff= 0.0005005005931165186
-------------------------------------- it=27 U=2.00 --------------------------------------
GA root convergence message---------------------------------
sucess= True
CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL
V= [ 0.18845962+0.j  0.18845702+0.j -0.07609861+0.j]
eb= [-0.10330001  0.10329167 -0.00000059]
V(ED)= [[ 0.18845962+0.j  0.        +0.j]
 [ 0.        +0.j  0.18845962+0.j]
 [ 0.18845702+0.j  0.        +0.j]
 [ 0.        +0.j  0.18845702+0.j]
 [-0.07609861+0.j -0.        +0.j]
 [-0.        +0.j -0.07609861+0.j]]
eb(ED)= [-0.10330001 -0.10330001  0.10329167  0.10329167 -0.00000059 -0.00000059]
Egs= -1.3506708771671951
evals= [0.         0.02282323 0.02282323 0.02282585 0.02282585 0.03813507
 0.03813507 0.03813507 0.05914283 0.05914674]
dm=
[[ 0.50000002  0.         -0.18705802  0.         -0.18706278 -0.
   0.20779573 -0.        ]
 [ 0.          0.50000002  0.         -0.18705802 -0.         -0.18706278
   0.          0.20779573]
 [-0.18705802  0.   

dm=
[[ 0.49999998 -0.         -0.18705831 -0.         -0.18706246 -0.
   0.20779572 -0.        ]
 [-0.          0.49999998 -0.         -0.18705831  0.         -0.18706246
  -0.          0.20779572]
 [-0.18705831 -0.          0.84827239 -0.         -0.00000622  0.
   0.24130134  0.        ]
 [-0.         -0.18705831 -0.          0.84827239  0.         -0.00000622
  -0.          0.24130134]
 [-0.18706246  0.         -0.00000622  0.          0.15173955 -0.
  -0.24130844  0.        ]
 [-0.         -0.18706246  0.         -0.00000622 -0.          0.15173955
   0.         -0.24130844]
 [ 0.20779572 -0.          0.24130134 -0.         -0.24130844  0.
   0.49999387  0.        ]
 [-0.          0.20779572  0.          0.24130134  0.         -0.24130844
   0.          0.49999387]]
trace(dm)= 4.000011578937031
docc= 0.06973921026529939
diff= 5.841069438705146e-05
-------------------------------------- it=33 U=2.00 --------------------------------------
GA root convergence message------------------